In [ ]:
pip install tifffile

In [ ]:
import bioformats
import javabridge
import numpy as np
from skimage import io

def max_intensity_projection(lif_path, output_path, series=0):
    # Start the Java Virtual Machine
    javabridge.start_vm(class_path=bioformats.JARS, run_headless=True)
    
    # Read the metadata
    omexml_str = bioformats.get_omexml_metadata(lif_path)
    omexml = bioformats.OMEXML(omexml_str)
    image_meta = omexml.image(series)
    pixels_meta = image_meta.Pixels
    
    # Total number of Z slices
    size_z = pixels_meta.SizeZ
    
    # Initialize reader
    reader = bioformats.ImageReader(lif_path, perform_init=True)

    # Initialize an empty array to hold the stack for both channels
    stack_ch1 = []
    stack_ch2 = []

    # Loop over each z-slice
    for z in range(size_z):
        # Read the image for the current Z slice
        # Assuming the pattern is odd slices for channel 1, even slices for channel 2
        if z % 2 == 0:  # Even slices for channel 2 (green)
            img_ch2 = reader.read(z=z, t=0, series=series, rescale=False, channel=0)
            stack_ch2.append(img_ch2)
        else:  # Odd slices for channel 1 (magenta)
            img_ch1 = reader.read(z=z, t=0, series=series, rescale=False, channel=0)
            stack_ch1.append(img_ch1)

    # Perform max intensity projection for each channel
    mip_ch1 = np.max(np.stack(stack_ch1), axis=0)
    mip_ch2 = np.max(np.stack(stack_ch2), axis=0)
    
    # Normalize to the range of 0-255 if they are not already in that range
    mip_ch1 = ((mip_ch1 / mip_ch1.max()) * 255).astype(np.uint8)
    mip_ch2 = ((mip_ch2 / mip_ch2.max()) * 255).astype(np.uint8)
    
    # Create an RGB image
    # Channel 1 (magenta) is red + blue, Channel 2 (green) is just green
    rgb_image = np.stack([
        mip_ch1,  # Red
        mip_ch2,  # Green
        mip_ch1   # Blue
    ], axis=-1)

    # Save the RGB max intensity projection as a TIFF
    io.imsave(output_path, rgb_image)

    # Close the reader
    reader.close()

    # Shut down the JVM
    javabridge.kill_vm()

# Use the function
max_intensity_projection('path/to/your/file.lif', 'path/to/output/max_projection_rgb.tiff')


In [1]:


import numpy as np
import tifffile as tiff
from skimage import io

def max_intensity_projection_ome_tiff(ome_tiff_path, output_path):
    # Read the OME-TIFF stack
    with tiff.TiffFile(ome_tiff_path) as tif:
        # Assuming the OME-TIFF has two channels interleaved in Z
        # Extract images for both channels
        stack_ch1 = []
        stack_ch2 = []

        '''for i, series in enumerate(tif.series):
            images = series.asarray()
            # Check if the series is even (0-indexed) or odd
            if i % 2 == 0:  # Channel 2 (green)
                stack_ch2.append(images)
            else:  # Channel 1 (magenta)
                stack_ch1.append(images)'''

        for i, series in enumerate(tif.series):
            images = series.asarray()
            print(f"Series {i}, shape: {images.shape}")  # Add this line to print shapes
            # Check if the series is even (0-indexed) or odd
            if i % 2 == 0:  # Channel 2 (green)
                stack_ch2.append(images)
            else:  # Channel 1 (magenta)
                stack_ch1.append(images)

        # Perform max intensity projection
        mip_ch1 = np.max(np.stack(stack_ch1), axis=0)
        mip_ch2 = np.max(np.stack(stack_ch2), axis=0)

        # Normalize to the range of 0-255 if not already in that range
        mip_ch1 = ((mip_ch1 / mip_ch1.max()) * 255).astype(np.uint8)
        mip_ch2 = ((mip_ch2 / mip_ch2.max()) * 255).astype(np.uint8)

        # Create an RGB image
        # Channel 1 (magenta) is red + blue, Channel 2 (green) is just green
        rgb_image = np.zeros((mip_ch1.shape[0], mip_ch1.shape[1], 3), dtype=np.uint8)
        rgb_image[..., 0] = mip_ch1  # Red
        rgb_image[..., 1] = mip_ch2  # Green
        rgb_image[..., 2] = mip_ch1  # Blue

    # Save the RGB max intensity projection as a TIFF
    io.imsave(output_path, rgb_image)



# Use the function
max_intensity_projection_ome_tiff('/Users/katherineridley/testtiff2_B_2_M04_OC_DGG_P+_031123_1.ome.tiff', '/Users/katherineridley/Dropbox (UK Dementia Research Institute)/KRidley/imaging/example images/max_projection_rgb.tiff')


Series 0, shape: (26, 2, 1024, 1024)
Series 1, shape: (26, 2, 1024, 1024)
Series 2, shape: (50, 2, 1024, 1024)
Series 3, shape: (50, 2, 1024, 1024)
Series 4, shape: (24, 2, 1024, 1024)
Series 5, shape: (24, 2, 1024, 1024)
Series 6, shape: (24, 2, 1024, 1024)
Series 7, shape: (49, 2, 1024, 1024)
Series 8, shape: (38, 2, 1024, 1024)
Series 9, shape: (38, 2, 1024, 1024)
Series 10, shape: (17, 2, 1024, 1024)
Series 11, shape: (17, 2, 1024, 1024)
Series 12, shape: (38, 2, 1024, 1024)
Series 13, shape: (38, 2, 1024, 1024)
Series 14, shape: (18, 2, 1024, 1024)
Series 15, shape: (18, 2, 1024, 1024)


ValueError: all input arrays must have the same shape

In [3]:
import numpy as np
import tifffile as tiff
from skimage import io

def max_intensity_projection_ome_tiff(ome_tiff_path, output_path):
    # Read the OME-TIFF stack
    with tiff.TiffFile(ome_tiff_path) as tif:
        # Initialize max projections with the first image
        max_projection_ch1 = None
        max_projection_ch2 = None

        for i, series in enumerate(tif.series):
            # Get the data for the current series
            images = series.asarray()
            # Iterate over each Z-slice
            for z_slice in images:
                # Separate channels assuming the first channel is at index 0 and the second at index 1
                ch1 = z_slice[0, ...]
                ch2 = z_slice[1, ...]

                # Update max projections for each channel
                if max_projection_ch1 is None or np.max(ch1) > np.max(max_projection_ch1):
                    max_projection_ch1 = ch1
                if max_projection_ch2 is None or np.max(ch2) > np.max(max_projection_ch2):
                    max_projection_ch2 = ch2

        # Normalize to the range of 0-255 if not already in that range
        mip_ch1 = ((max_projection_ch1 / max_projection_ch1.max()) * 255).astype(np.uint8)
        mip_ch2 = ((max_projection_ch2 / max_projection_ch2.max()) * 255).astype(np.uint8)

        # Create an RGB image where Channel 1 (magenta) is red + blue, Channel 2 (green) is green
        rgb_image = np.stack([mip_ch1, mip_ch2, mip_ch1], axis=-1)

        # Save the RGB max intensity projection as a TIFF
        io.imsave(output_path, rgb_image)
# Use the function
max_intensity_projection_ome_tiff('/Users/katherineridley/testtiff2_B_2_M04_OC_DGG_P+_031123_1.ome.tiff', '/Users/katherineridley/Dropbox (UK Dementia Research Institute)/KRidley/imaging/example images/max_projection_rgb.tiff')


In [4]:
import tifffile as tiff

# Path to your OME-TIFF file
ome_tiff_path = '/Users/katherineridley/testtiff2_B_2_M04_OC_DGG_P+_031123_1.ome.tiff'

# Read the OME-TIFF file
with tiff.TiffFile(ome_tiff_path) as tif:
    # Access the OME metadata
    ome_metadata = tif.ome_metadata

    # Print the raw XML metadata
    print(ome_metadata)

    # If you want a nicer output, you might need to parse the XML
    # This requires the xml.etree.ElementTree library (or similar)
    import xml.etree.ElementTree as ET
    xml_root = ET.fromstring(ome_metadata)

    # Print out all XML tags and text
    for elem in xml_root.iter():
        print(f'{elem.tag}: {elem.text}')
        for attr, value in elem.attrib.items():
            print(f'  @{attr}: {value}')


<?xml version="1.0" encoding="UTF-8"?><!-- Warning: this comment is an OME-XML metadata block, which contains crucial dimensional parameters and other important metadata. Please edit cautiously (if at all), and back up the original data before doing so. For more information, see the OME-TIFF web site: https://docs.openmicroscopy.org/latest/ome-model/ome-tiff/. --><OME xmlns="http://www.openmicroscopy.org/Schemas/OME/2016-06" xmlns:xsi="http://www.w3.org/2001/XMLSchema-instance" Creator="OME Bio-Formats 6.0.1" UUID="urn:uuid:82a53f89-4063-4098-adfb-97cf96f06d73" xsi:schemaLocation="http://www.openmicroscopy.org/Schemas/OME/2016-06 http://www.openmicroscopy.org/Schemas/OME/2016-06/ome.xsd"><Instrument ID="Instrument:0"><Microscope Type="Other"/><Laser ID="LightSource:0:0" LaserMedium="Other" Type="Other" Wavelength="488.0" WavelengthUnit="nm"/><Laser ID="LightSource:0:1" LaserMedium="Other" Type="Other" Wavelength="552.0" WavelengthUnit="nm"/><Laser ID="LightSource:0:2" LaserMedium="Othe

In [5]:
import xml.etree.ElementTree as ET

# Parse the XML metadata
xml_root = ET.fromstring(ome_metadata)

# Find and print information about each image series
for image in xml_root.findall('{http://www.openmicroscopy.org/Schemas/OME/2016-06}Image'):
    print(f"Image ID: {image.get('ID')}")
    pixels = image.find('{http://www.openmicroscopy.org/Schemas/OME/2016-06}Pixels')
    if pixels is not None:
        size_x = pixels.get('SizeX')
        size_y = pixels.get('SizeY')
        size_z = pixels.get('SizeZ')
        size_c = pixels.get('SizeC')
        size_t = pixels.get('SizeT')
        dimension_order = pixels.get('DimensionOrder')
        print(f"  Size (XYZCT): ({size_x}, {size_y}, {size_z}, {size_c}, {size_t})")
        print(f"  Dimension Order: {dimension_order}")

        # Check if channels are interleaved
        interleaved = dimension_order.startswith("XYC") or dimension_order.startswith("CYX")
        print(f"  Channels interleaved: {interleaved}")


Image ID: Image:0
  Size (XYZCT): (1024, 1024, 26, 2, 1)
  Dimension Order: XYCZT
  Channels interleaved: True
Image ID: Image:1
  Size (XYZCT): (1024, 1024, 26, 2, 1)
  Dimension Order: XYCZT
  Channels interleaved: True
Image ID: Image:2
  Size (XYZCT): (1024, 1024, 50, 2, 1)
  Dimension Order: XYCZT
  Channels interleaved: True
Image ID: Image:3
  Size (XYZCT): (1024, 1024, 50, 2, 1)
  Dimension Order: XYCZT
  Channels interleaved: True
Image ID: Image:4
  Size (XYZCT): (1024, 1024, 24, 2, 1)
  Dimension Order: XYCZT
  Channels interleaved: True
Image ID: Image:5
  Size (XYZCT): (1024, 1024, 24, 2, 1)
  Dimension Order: XYCZT
  Channels interleaved: True
Image ID: Image:6
  Size (XYZCT): (1024, 1024, 24, 2, 1)
  Dimension Order: XYCZT
  Channels interleaved: True
Image ID: Image:7
  Size (XYZCT): (1024, 1024, 49, 2, 1)
  Dimension Order: XYCZT
  Channels interleaved: True
Image ID: Image:8
  Size (XYZCT): (1024, 1024, 38, 2, 1)
  Dimension Order: XYCZT
  Channels interleaved: True
I

In [6]:
import numpy as np
import tifffile as tiff
from skimage import io

def max_intensity_projection_ome_tiff(ome_tiff_path, output_path):
    # Read the OME-TIFF stack
    with tiff.TiffFile(ome_tiff_path) as tif:
        # Get the OME metadata
        ome_metadata = tif.ome_metadata

        # Create empty lists to hold the max intensity projections
        max_projections = []

        for series_index, series in enumerate(tif.series):
            # Set the series
            tif.set_series(series_index)
            
            # Read the image stack for this series
            stack = tif.asarray()
            
            # Determine the number of channels (assumed to be 2 based on the metadata)
            num_channels = 2
            
            # Split the channels
            # The stack is in the shape of (Z, C, Y, X), and we want to split it based on C
            channels = [stack[:, i, :, :] for i in range(num_channels)]
            
            # Perform max intensity projection for each channel
            for ch in channels:
                max_projection = np.max(ch, axis=0)
                max_projections.append(max_projection)
        
        # Assume first channel is magenta and second is green
        # Stack and normalize the projections for both channels
        mip_ch1 = ((max_projections[0::2][0] / max_projections[0::2][0].max()) * 255).astype(np.uint8)
        mip_ch2 = ((max_projections[1::2][0] / max_projections[1::2][0].max()) * 255).astype(np.uint8)

        # Create an RGB image
        # Channel 1 (magenta) is red + blue, Channel 2 (green) is just green
        rgb_image = np.zeros((mip_ch1.shape[0], mip_ch1.shape[1], 3), dtype=np.uint8)
        rgb_image[..., 0] = mip_ch1  # Red
        rgb_image[..., 1] = mip_ch2  # Green
        rgb_image[..., 2] = mip_ch1  # Blue

        # Save the RGB max intensity projection as a TIFF
        io.imsave(output_path, rgb_image)

# Use the function
max_intensity_projection_ome_tiff(
    '/Users/katherineridley/testtiff2_B_2_M04_OC_DGG_P+_031123_2.ome.tiff', 
    '/Users/katherineridley/Dropbox (UK Dementia Research Institute)/KRidley/imaging/example images/max_projection_rgb.tiff'
)


AttributeError: 'TiffFile' object has no attribute 'set_series'

In [7]:
import numpy as np
import tifffile as tiff
from skimage import io

def max_intensity_projection_ome_tiff(ome_tiff_path, output_path):
    with tiff.TiffFile(ome_tiff_path) as tif:
        # Initialize lists to store max intensity projections for each channel
        max_projection_ch1 = None
        max_projection_ch2 = None
        
        for series in tif.series:
            # Assuming the structure is (Z, C, Y, X) based on interleaved channels
            stack = series.asarray()
            # Split the channels, assuming the second axis is channel
            ch1 = stack[:, 0, :, :]
            ch2 = stack[:, 1, :, :]
            
            # Perform max intensity projection across the Z-axis (axis=0)
            mip_ch1 = np.max(ch1, axis=0)
            mip_ch2 = np.max(ch2, axis=0)
            
            # Update the max projection with the current one if it's greater
            if max_projection_ch1 is None:
                max_projection_ch1 = mip_ch1
                max_projection_ch2 = mip_ch2
            else:
                max_projection_ch1 = np.maximum(max_projection_ch1, mip_ch1)
                max_projection_ch2 = np.maximum(max_projection_ch2, mip_ch2)

        # Normalize to the range of 0-255 if not already in that range
        max_projection_ch1 = ((max_projection_ch1 / max_projection_ch1.max()) * 255).astype(np.uint8)
        max_projection_ch2 = ((max_projection_ch2 / max_projection_ch2.max()) * 255).astype(np.uint8)

        # Create an RGB image
        # Channel 1 (magenta) is red + blue, Channel 2 (green) is just green
        rgb_image = np.zeros((max_projection_ch1.shape[0], max_projection_ch1.shape[1], 3), dtype=np.uint8)
        rgb_image[..., 0] = max_projection_ch1  # Red
        rgb_image[..., 1] = max_projection_ch2  # Green
        rgb_image[..., 2] = max_projection_ch1  # Blue

        # Save the RGB max intensity projection as a TIFF
        io.imsave(output_path, rgb_image)

# Use the function

max_intensity_projection_ome_tiff(
    '/Users/katherineridley/testtiff2_B_2_M04_OC_DGG_P+_031123_2.ome.tiff', 
    '/Users/katherineridley/Dropbox (UK Dementia Research Institute)/KRidley/imaging/example images/max_projection_rgb.tiff'
)




In [10]:
pip install opencv-python


   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 54.7/54.7 MB 16.6 MB/s eta 0:00:0000:0100:01
Note: you may need to restart the kernel to use updated packages.


In [13]:
import cv2
import numpy as np

# Read the max projection image
max_projection_image_path = '/Users/katherineridley/Dropbox (UK Dementia Research Institute)/KRidley/imaging/example images/max_projection_rgb.tiff'
max_projection_image = cv2.imread(max_projection_image_path)

# Set contrast and brightness values
contrast = 1.5  # for example, 1.0 means no change, 1.2 is increased contrast
brightness = -100 # value range can be from -255 to 255, 0 means no change

# Apply the transformation
adjusted_image = cv2.convertScaleAbs(max_projection_image, alpha=contrast, beta=brightness)

# Save the result
output_image_path = '/Users/katherineridley/Dropbox (UK Dementia Research Institute)/KRidley/imaging/example images/max_projection_rgb2.tiff'
cv2.imwrite(output_image_path, adjusted_image)


True

In [14]:
import numpy as np
import tifffile as tiff
from skimage import io

def export_max_projections(ome_tiff_path, output_dir):
    with tiff.TiffFile(ome_tiff_path) as tif:
        max_projection_ch1 = None
        max_projection_ch2 = None

        for series in tif.series:
            stack = series.asarray()
            ch1 = stack[:, 0, :, :]
            ch2 = stack[:, 1, :, :]

            mip_ch1 = np.max(ch1, axis=0)
            mip_ch2 = np.max(ch2, axis=0)

            if max_projection_ch1 is None:
                max_projection_ch1 = mip_ch1
                max_projection_ch2 = mip_ch2
            else:
                max_projection_ch1 = np.maximum(max_projection_ch1, mip_ch1)
                max_projection_ch2 = np.maximum(max_projection_ch2, mip_ch2)

        # Normalize the projections
        max_projection_ch1 = ((max_projection_ch1 / max_projection_ch1.max()) * 255).astype(np.uint8)
        max_projection_ch2 = ((max_projection_ch2 / max_projection_ch2.max()) * 255).astype(np.uint8)

        # Save the max intensity projections of each channel
        io.imsave(f"{output_dir}/max_projection_ch1.tiff", max_projection_ch1)
        io.imsave(f"{output_dir}/max_projection_ch2.tiff", max_projection_ch2)

        # Create an RGB image for the overlay
        # Channel 1 (magenta) is red + blue, Channel 2 (green) is just green
        rgb_image = np.zeros((max_projection_ch1.shape[0], max_projection_ch1.shape[1], 3), dtype=np.uint8)
        rgb_image[..., 0] = max_projection_ch1  # Red
        rgb_image[..., 1] = max_projection_ch2  # Green
        rgb_image[..., 2] = max_projection_ch1  # Blue

        # Save the RGB max intensity projection
        io.imsave(f"{output_dir}/max_projection_rgb.tiff", rgb_image)

# Example usage
export_max_projections('/Users/katherineridley/testtiff2_B_2_M04_OC_DGG_P+_031123_2.ome.tiff', 
    '/Users/katherineridley/Dropbox (UK Dementia Research Institute)/KRidley/imaging/example images/'
)


In [17]:
import cv2
import numpy as np
import tifffile as tiff
from skimage import io

def apply_clahe(image, clip_limit=1.0, tile_grid_size=(8, 8)):
    # Convert the image to a format suitable for CLAHE
    image = image.astype(np.uint8)
    # Create a CLAHE object
    clahe = cv2.createCLAHE(clipLimit=clip_limit, tileGridSize=tile_grid_size)
    # Apply CLAHE to the image
    return clahe.apply(image)

def export_max_projections_with_clahe(ome_tiff_path, output_dir):
    with tiff.TiffFile(ome_tiff_path) as tif:
        max_projection_ch1 = None
        max_projection_ch2 = None

        for series in tif.series:
            stack = series.asarray()
            ch1 = stack[:, 0, :, :]
            ch2 = stack[:, 1, :, :]

            mip_ch1 = np.max(ch1, axis=0)
            mip_ch2 = np.max(ch2, axis=0)

            if max_projection_ch1 is None:
                max_projection_ch1 = mip_ch1
                max_projection_ch2 = mip_ch2
            else:
                max_projection_ch1 = np.maximum(max_projection_ch1, mip_ch1)
                max_projection_ch2 = np.maximum(max_projection_ch2, mip_ch2)

        # Normalize and apply CLAHE
        max_projection_ch1 = apply_clahe(((max_projection_ch1 / max_projection_ch1.max()) * 255).astype(np.uint8))
        max_projection_ch2 = apply_clahe(((max_projection_ch2 / max_projection_ch2.max()) * 255).astype(np.uint8))

        # Save the max intensity projections of each channel
        io.imsave(f"{output_dir}/max_projection_ch1_clahe.tiff", max_projection_ch1)
        io.imsave(f"{output_dir}/max_projection_ch2_clahe.tiff", max_projection_ch2)

        # Create an RGB image for the overlay
        rgb_image = np.zeros((max_projection_ch1.shape[0], max_projection_ch1.shape[1], 3), dtype=np.uint8)
        rgb_image[..., 0] = max_projection_ch1  # Red
        rgb_image[..., 1] = max_projection_ch2  # Green
        rgb_image[..., 2] = max_projection_ch1  # Blue

        # Save the RGB max intensity projection with CLAHE
        io.imsave(f"{output_dir}/max_projection_rgb_clahe.tiff", rgb_image)

# Example usage
export_max_projections_with_clahe('/Users/katherineridley/testtiff2_B_2_M04_OC_DGG_P+_031123_2.ome.tiff', 
    '/Users/katherineridley/Dropbox (UK Dementia Research Institute)/KRidley/imaging/example images/'
)


In [22]:
pip install scikit-learn

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 10.2/10.2 MB 20.6 MB/s eta 0:00:0000:010:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 302.2/302.2 kB 22.0 MB/s eta 0:00:00
Note: you may need to restart the kernel to use updated packages.


In [1]:
pip install ut


Note: you may need to restart the kernel to use updated packages.


In [2]:
from ij import IJ, ImagePlus
from ij.plugin import ZProjector
from ij.io import FileSaver
import pandas as pd

def max_intensity_projection(ome_tiff_path, output_path):
    # Open the OME-TIFF file
    imp = IJ.openImage(ome_tiff_path)
    if imp is None:
        print("Could not open image from path:", ome_tiff_path)
        return

    # Create a ZProjector for max intensity projection
    project = ZProjector(imp)
    project.setMethod(ZProjector.MAX_METHOD)

    # Do the projection for each channel
    n_channels = imp.getNChannels()
    for ch in range(1, n_channels + 1):
        imp.setC(ch)
        project.doProjection()
        projection = project.getProjection()

        # Save the projection
        ch_output_path = output_path.replace('.tiff', '_ch{}.tiff'.format(ch))
        FileSaver(projection).saveAsTiff(ch_output_path)
        print("Saved channel", ch, "projection to", ch_output_path)

    # Close the original image
    imp.close()

# Example usage
ome_tiff_path = '/Users/katherineridley/testtiff2_B_2_M04_OC_DGG_P+_031123_2.ome.tiff'
output_path = '/Users/katherineridley/testimagejz.tiff'
max_intensity_projection(ome_tiff_path, output_path)


: 